<a href="https://colab.research.google.com/github/Padmashree02/Object_detection-Social_distancing-/blob/main/Main_code.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [1]:
#imported required libraries

import cv2
import numpy as np
import matplotlib.pyplot as plt

!pip install moviepy

from moviepy.editor import VideoFileClip

In [2]:
#Load the model file and config file
model_file = '/content/MobileNetSSD_deploy.caffemodel'
config_file = '/content/MobileNetSSD_deploy.prototxt'

#read the model or neural network
model=cv2.dnn.readNetFromCaffe(config_file,model_file)

In [3]:
class_file = '/content/coco.names'

with open (class_file,'rt') as f:
  classes=f.read().rstrip('\n').split('\n')

In [4]:
#Object detection process

#to display each class with different colors
COLORS = np.random.uniform(0, 255, size=(len(classes), 3))

def detection(frame,model):

  #the new list variable
  results=[]
  box=[]

  #define the height and width wrt image's dimension
  rows=frame.shape[0]  #rows
  cols=frame.shape[1]

  #Default values
  img_size=300
  mean=[127.5,127.5,127.5]

  #convert the image into network understanding format (blob)
  blob=cv2.dnn.blobFromImage(frame,0.007843,(img_size,img_size),mean)

  #Set the input data to the DenseNet model
  model.setInput(blob)

  #pass the image into network
  detected_obj=model.forward()

  #process each detection
  for object in np.arange(0,detected_obj.shape[2]):

    #Extract the classID
    class_id=int(detected_obj[0,0,object,1])

    #Extract all scores detected wrt each class
    confidence_score=float(detected_obj[0,0,object,2])

    #Checking whether the the object has been detected good or bad
    #As well as accept those object classified class as the people (class as 'people')
    if confidence_score > 0.7 and class_id==15:

      #convert the normalized coordinates to origional coordinates wrt defined image's shape
      x=int(detected_obj[0,0,object,3]*cols)
      y=int(detected_obj[0,0,object,4]*rows)
      w=int(detected_obj[0,0,object,5]*cols-x)
      h=int(detected_obj[0,0,object,6]*rows-y)

      box=[x,y,w,h]

      #compute the center of the box
      center_x=int((box[0]+box[2])/2)
      center_y=int((box[1]+box[3])/2)

      #Append all values in respective list
      results.append((confidence_score,box,(center_x,center_y)))

  return results

In [5]:
#To compute the euclidean distance
def euclidean_dist(A,B):
  p1=np.sum(A**2,axis=1)[:,np.newaxis]
  p2=np.sum(B**2,axis=1)[:,np.newaxis]
  p3= -2*np.dot(A,B.T)
  return np.round(np.sqrt(p1+p2+p3),2)

In [9]:
#detect the social distancing among people
def detect_violations(results):

  violations=set()
  factor=2

  #if there are more than two people
  if len(results) >= 2:

    boxes_width=np.array([abs(int(r[1][2])) for r in results])
    centroids=np.array([r[2] for r in results])                 #stores the center_x and center_y
    distance_matrix=euclidean_dist(centroids, centroids)        #computes the euclidean distance

    #check whether distance with each person are safe or not safe
    for row in range(distance_matrix.shape[0]):
      for col in range(row+1,distance_matrix.shape[1]):

        #Presume unsafe if closer than 1.2x (fac) width of a person apart.
        diff_disatance=int(factor*min(boxes_width[row],boxes_width[col]))

        if distance_matrix[row,col] < diff_disatance:
          violations.add(row)
          violations.add(col)

  return violations

In [10]:
#Load the video
video='/content/input.mp4'
cap=cv2.VideoCapture(video)

#video dimensions/resolution (to get the video's properties) - width, height, frames per second
video_width=int(cap.get(cv2.CAP_PROP_FRAME_WIDTH))
video_height=int(cap.get(cv2.CAP_PROP_FRAME_HEIGHT))
fps=int(cap.get(cv2.CAP_PROP_FPS))

#Procedure to form the file for saving the output video
output_filepath='social_distance.mp4'

#file name in which video to be saved
fourcc=cv2.VideoWriter_fourcc(*'mp4v')
out=cv2.VideoWriter(output_filepath,fourcc,fps,(video_width,video_height))

frame_rate=0

#Capturing the video into frames
while cap.isOpened():

  retival,frame=cap.read()
  if not retival:
    print("End of video stream")
    break

  #Calling all the defined fucntions

  #Detects the objects on the input image
  results=detection(frame, model)

  #Recognise whether the person is safe or not safe
  violations=detect_violations(results)

  for index,(confidence,bounding_box,centroid) in enumerate(results):

    #Extract each element from bounding box list
    start_x,start_y,end_x,end_y=bounding_box

    #set an unique color for label 'safe' and label 'not safe'
    color = (0, 0, 255) if index in violations else (0, 255, 0)

    #Draw the bounding box to display the detected object
    cv2.rectangle(frame, (start_x, start_y), (start_x+end_x, start_y+end_y), color, 2)

    #Display the class name
    cv2.putText(frame,'Not safe' if index in violations else 'Safe', (start_x,start_y-10),cv2.FONT_HERSHEY_SIMPLEX,0.6,color,2)

  #save the resultant video by storing each current frames
  out.write(frame)
  #print(frame_rate)

  #To terminate the video after fixed or specified count (frame_rate)
  frame_rate=frame_rate+1
  if frame_rate==250:
    break

cap.release()
out.release()

#Disply of the resultant video
vid=VideoFileClip(output_filepath)
vid.ipython_display(width=600)

  return np.round(np.sqrt(p1+p2+p3),2)



Moviepy - Building video __temp__.mp4.
Moviepy - Writing video __temp__.mp4



Moviepy - Done !
Moviepy - video ready __temp__.mp4
